Necessary imports and helper functions for displaying points, boxes, and masks.

In [1]:
import os
# if using Apple MPS, fall back to CPU for unsupported ops
os.environ["PYTORCH_ENABLE_MPS_FALLBACK"] = "1"
import numpy as np
import torch
import matplotlib.pyplot as plt
from PIL import Image
import cv2
import numpy as np





In [2]:
# select the device for computation
if torch.cuda.is_available():
    device = torch.device("cuda")
elif torch.backends.mps.is_available():
    device = torch.device("mps")
else:
    device = torch.device("cpu")
print(f"using device: {device}")

if device.type == "cuda":
    # use bfloat16 for the entire notebook
    torch.autocast("cuda", dtype=torch.bfloat16).__enter__()
    # turn on tfloat32 for Ampere GPUs (https://pytorch.org/docs/stable/notes/cuda.html#tensorfloat-32-tf32-on-ampere-devices)
    if torch.cuda.get_device_properties(0).major >= 8:
        torch.backends.cuda.matmul.allow_tf32 = True
        torch.backends.cudnn.allow_tf32 = True
elif device.type == "mps":
    print(
        "\nSupport for MPS devices is preliminary. SAM 2 is trained with CUDA and might "
        "give numerically different outputs and sometimes degraded performance on MPS. "
        "See e.g. https://github.com/pytorch/pytorch/issues/84936 for a discussion."
    )

using device: cuda


In [3]:
np.random.seed(3)

def show_mask(mask, ax, random_color=False, borders = True):
    if random_color:
        color = np.concatenate([np.random.random(3), np.array([0.6])], axis=0)
    else:
        color = np.array([30/255, 144/255, 255/255, 0.6])
    h, w = mask.shape[-2:]
    mask = mask.astype(np.uint8)
    mask_image =  mask.reshape(h, w, 1) * color.reshape(1, 1, -1)
    if borders:
        import cv2
        contours, _ = cv2.findContours(mask,cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_NONE) 
        # Try to smooth contours
        contours = [cv2.approxPolyDP(contour, epsilon=0.01, closed=True) for contour in contours]
        mask_image = cv2.drawContours(mask_image, contours, -1, (1, 1, 1, 0.5), thickness=2) 
    ax.imshow(mask_image)

def show_points(coords, labels, ax, marker_size=375):
    pos_points = coords[labels==1]
    neg_points = coords[labels==0]
    ax.scatter(pos_points[:, 0], pos_points[:, 1], color='green', marker='*', s=marker_size, edgecolor='white', linewidth=1.25)
    ax.scatter(neg_points[:, 0], neg_points[:, 1], color='red', marker='*', s=marker_size, edgecolor='white', linewidth=1.25)   

def show_box(box, ax):
    x0, y0 = box[0], box[1]
    w, h = box[2] - box[0], box[3] - box[1]
    ax.add_patch(plt.Rectangle((x0, y0), w, h, edgecolor='green', facecolor=(0, 0, 0, 0), lw=2))    

def show_and_save_masks(image, masks, scores, point_coords=None, box_coords=None, input_labels=None, borders=True, save_path = None):
    for i, (mask, score) in enumerate(zip(masks, scores)):
        plt.figure(figsize=(10, 10))
        plt.imshow(image)
        show_mask(mask, plt.gca(), borders=borders)
        if point_coords is not None:
            assert input_labels is not None
            show_points(point_coords, input_labels, plt.gca())
        if box_coords is not None:
            # boxes
            show_box(box_coords, plt.gca())
        if len(scores) > 1:
            plt.title(f"Mask {i+1}, Score: {score:.3f}", fontsize=18)
        plt.axis('off')
        plt.savefig(save_path)
        plt.clf()
        # plt.show()
        
def mask_to_polygons(binary_mask):
    """
    바이너리 마스크를 폴리곤 리스트로 변환하는 함수
    :param binary_mask: (H, W) 또는 (1, H, W) 형태의 numpy 배열 (dtype: np.uint8, 값: 0 또는 1)
    :return: 폴리곤 리스트 (각 폴리곤은 [[x1, y1], [x2, y2], ...] 형태)
    """
    if len(binary_mask.shape) == 3:
        binary_mask = binary_mask.squeeze(0)  # (1, H, W) -> (H, W)
    
    binary_mask = (binary_mask * 255).astype(np.uint8)  # 0과 1을 0과 255로 변환
    contours, _ = cv2.findContours(binary_mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    polygons = []
    for contour in contours:
        polygon = contour.reshape(-1, 2).tolist()  # [[x1, y1], [x2, y2], ...] 형태로 변환
        polygons.append(polygon)

    return polygons

def draw_polygons(image, polygons, color=(0, 255, 0), thickness=3):
    """
    원본 이미지 위에 폴리곤을 그리는 함수
    :param image: (H, W, 3) 형태의 원본 이미지 (numpy 배열)
    :param polygons: 폴리곤 리스트 (각 폴리곤은 [[x1, y1], [x2, y2], ...] 형태)
    :param color: 폴리곤 색상 (기본값: 녹색)
    :param thickness: 선의 두께 (기본값: 3)
    :return: 폴리곤이 그려진 이미지
    """
    image_copy = image.copy()
    for polygon in polygons:
        pts = np.array(polygon, np.int32).reshape((-1, 1, 2))
        cv2.polylines(image_copy, [pts], isClosed=True, color=color, thickness=thickness)
    return image_copy

# SAM의 추론 결과를 통해 Masked image와 labelme polygon label 파일을 만들고 저장

In [4]:
from sam2.build_sam import build_sam2
from sam2.sam2_image_predictor import SAM2ImagePredictor

sam2_checkpoint = "../checkpoints/sam2.1_hiera_large.pt"
model_cfg = "configs/sam2.1/sam2.1_hiera_l.yaml"

sam2_model = build_sam2(model_cfg, sam2_checkpoint, device=device)

predictor = SAM2ImagePredictor(sam2_model)

In [5]:
labelme_label = {
  "version": "5.6.1",
  "flags": {},
  "shapes": [
    {
      "label": "bottle",
      "points": [
        [ 100, 100 ]
      ],
      "group_id": None,
      "description": "",
      "shape_type": "polygon",
      "flags": {},
      "mask": None
    }
  ],
  "imagePath": "1.jpg",
  "imageData": None,
  "imageHeight": 1080,
  "imageWidth": 1920
}

In [2]:

    
from pathlib import Path
from IPython.display import clear_output
import itertools
import json
import gc


def generage_sam_infered_labelme_label_file(img_path, labelme_path):
    try:
        image = Image.open(img_path)
        image = np.array(image.convert("RGB"))
        # image = gray_world_white_balance(image)
        
        
        # image[acc_mask == 1] = [0, 0, 0]
        predictor.set_image(image)
        
        label_path = str(img_path).replace("images", "point_labels").replace(img_path.suffix, ".json")
        new_label_path = str(img_path).replace("images", "mask_labels").replace(img_path.suffix, ".json")
        
        print(img_path)
        print(label_path)
        
        with open(label_path) as f:
            label = json.load(f)
            
        points = [shape["points"][0] for shape in label["shapes"]]
        points = [[int(x), int(y)] for x, y in points]
        
        input_point = np.array(points)
        input_label = np.array([1]*len(points))
    
        masks, scores, logits = predictor.predict(
            point_coords=input_point,
            point_labels=input_label,
            multimask_output=True,
        )


        sorted_ind = np.argsort(scores)[::-1]
        masks = masks[sorted_ind]
        scores = scores[sorted_ind]
        logits = logits[sorted_ind]
        masks = masks[:1, :, :]
        scores = scores[:1]
        
        
        result_path = str(img_path).replace("images", "sam_masked_image")
        Path(result_path).parent.mkdir(parents=True, exist_ok=True)
        
        
        height, width, _= image.shape
        relative_image_path = os.path.relpath(img_path, labelme_path)
        polygons = mask_to_polygons(masks)
        polygon = max(polygons, key=len)
        
        
        

        
        labelme_label["shapes"][0]["points"] = polygon
        labelme_label["imagePath"] = relative_image_path
        labelme_label["imageData"] = None
        labelme_label["imageHeight"] = height
        labelme_label["imageWidth"] = width
        
        
        Path(new_label_path).parent.mkdir(parents=True, exist_ok=True)
        with open(new_label_path, "w", encoding="utf-8") as f:
            json.dump(labelme_label, f, ensure_ascii=False, indent=4)
            
            
        show_and_save_masks(image, masks, scores, point_coords=None, input_labels=input_label, borders=True, save_path = result_path)
        
    except Exception as e:
        print(e)





In [18]:
work_dir_path_list = [
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A"),
    # Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈"),
    # Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler2_우종윤"),
    # Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler3_송무건")
]



for work_dir_path in work_dir_path_list:
    labelme_path = work_dir_path/"labelme/labelme/__init__.py"

    dir_paths = itertools.chain(
        (work_dir_path/"1st/images").glob("*/*")
    )

    for dir_path in dir_paths:
        paths = itertools.chain(
            dir_path.rglob("*.png"),
            dir_path.rglob("*.jpg")
        )
        paths = sorted(paths, key=lambda x: int(x.stem))

        for img_path in paths:
            generage_sam_infered_labelme_label_file(img_path, labelme_path)        
            # show_and_save_masks(image, masks, scores, point_coords=input_point, input_labels=input_label, borders=True, save_path = result_path)
    gc.collect()

W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\1.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\1.json
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\2.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\2.json
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\3.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\3.json
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\4.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\4.json
W:\wine\wine_recognition\WORK_dataset_collection\dat

C:\Users\admin\AppData\Local\Temp\ipykernel_41568\1264987239.py:32: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`). Consider using `matplotlib.pyplot.close()`.
  plt.figure(figsize=(10, 10))


W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\22.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\22.json
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\23.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\23.json
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\24.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\24.json
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\images\LB230\C1\25.jpg
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler4_A\1st\point_labels\LB230\C1\25.json
W:\wine\wine_recognition\WORK_dataset_collec

KeyboardInterrupt: 

<Figure size 1000x1000 with 0 Axes>

...

<Figure size 1000x1000 with 0 Axes>

<Figure size 1000x1000 with 0 Axes>

<Figure size 1000x1000 with 0 Axes>

<Figure size 1000x1000 with 0 Axes>

<Figure size 1000x1000 with 0 Axes>

# SAM 추론을 통해 얻은 Polygon의 점 수를 줄여 단순하게 만들고 저장


In [83]:
import json
import cv2
import numpy as np
import matplotlib.pyplot as plt

from IPython.display import clear_output




def ganerage_simplified_mask_from_sam_mask(work_dir_path):

    for path in (work_dir_path/"1st/mask_labels").rglob("*.json"):
        with open(path, "r") as f:
            mask_labels = json.load(f)
        polygon = mask_labels["shapes"][0]["points"]
        # print(polygon)
        polygon = np.array(polygon, dtype=np.int32)
        epsilon = 0.003 * cv2.arcLength(polygon, True)
        simplified_polygon = cv2.approxPolyDP(polygon, epsilon, True)
        simplified_polygon = simplified_polygon.squeeze(1).tolist()
        mask_labels["shapes"][0]["points"] = simplified_polygon
        
        
        save_path = Path(str(path).replace("mask_labels", "simplified_mask_labels"))
        
        save_path.parent.mkdir(parents=True, exist_ok=True)    
        with open(save_path, "w", encoding="utf-8") as f:
            json.dump(mask_labels, f, indent=4, ensure_ascii=False)  
    
work_dir_path_list = [
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈"),
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler2_우종윤"),
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler3_송무건")
]

for path in work_dir_path_list:
    ganerage_simplified_mask_from_sam_mask(path)
        

# 1차 검수 -> 어떤 이미지가 SAM 추론이 부정확한지 체크

# 2차 레이블링 준비: 레이블링 대상만 따로 추출

In [6]:
work_dir_path_list = [
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈"),
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler2_우종윤"),
    Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler3_송무건")
]

for work_dir_path in work_dir_path_list:
    with open(work_dir_path/"1st/wrong_image_path.json") as f:
        data = json.load(f)
    
    for img_path, result in data.items():
        img_path = img_path.replace("sam_masked_image", "images")
        img_path = Path(img_path)
        if result["error"]:
            
            
            sam_masked_image_path = str(img_path).replace("images", "sam_masked_image").replace(img_path.suffix, ".jpg")
            point_label_path = str(img_path).replace("images", "point_labels").replace(img_path.suffix, ".json")
            mask_label_path = str(img_path).replace("images", "mask_labels").replace(img_path.suffix, ".json")
            simplified_mask_label_path = str(img_path).replace("images", "simplified_mask_labels").replace(img_path.suffix, ".json")
            
            for path in [img_path, sam_masked_image_path, point_label_path, mask_label_path, simplified_mask_label_path]:
                path = work_dir_path/path
                target_path = Path(str(path).replace("1st", "2nd"))
                target_path.parent.mkdir(parents=True, exist_ok=True)
                shutil.copy(path, target_path)
    
    for point_label_path in (work_dir_path/"2nd"/"point_labels").rglob("*.json"):
        with open(point_label_path, "r") as f:
            data = json.load(f)    
            point_shape = data["shapes"]
            
        mask_label_path = str(point_label_path).replace("point_labels", "mask_labels")
        target_mask_label_path = str(point_label_path).replace("point_labels", "mask___point___labels")
        mask_label_simplified_path = str(point_label_path).replace("point_labels", "simplified_mask_labels")
        target_mask_label_simplified_path = str(point_label_path).replace("point_labels", "simplified_mask___point_labels")
        
        for path, target_path in [(mask_label_path, target_mask_label_path), (mask_label_simplified_path, target_mask_label_simplified_path)]:
            with open(path, "r") as f:
                data = json.load(f)
            
            data["shapes"] = data["shapes"]+point_shape
            
            Path(target_path).parent.mkdir(parents=True, exist_ok=True)    
            with open(target_path, "w", encoding="utf-8") as f:
                json.dump(data, f, indent=4, ensure_ascii=False)  


In [97]:
for path in Path("W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment").rglob("*.json"):
    if path.name != "wrong_image_path.json":
        try:
            with open(path) as f:
                data = json.load(f)
            
            data["imagePath"] = data["imagePath"].replace("/1st", "")
            data["imagePath"] = data["imagePath"].replace("/2nd", "")
            
            with open(path, "w") as f:
                json.dump(data, f, ensure_ascii=False, indent=4)

        except Exception as e:
            print(e)
            print(path)
            continue
    

'imagePath'
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈\labelme\.vscode\launch.json
'imagePath'
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈\labelme\examples\instance_segmentation\data_dataset_coco\annotations.json
Expecting value: line 1 column 1 (char 0)
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈\labelme\tests\labelme_tests\data\annotated\2011_000003.json
Expecting value: line 1 column 1 (char 0)
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈\labelme\tests\labelme_tests\data\annotated\2011_000006.json
Expecting value: line 1 column 1 (char 0)
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assignment\Labeler1_한명훈\labelme\tests\labelme_tests\data\annotated\2011_000025.json
Expecting value: line 1 column 1 (char 0)
W:\wine\wine_recognition\WORK_dataset_collection\data\dynamic\work_assi